# sofia-py example 2
## Sampled unity plane wave simulation for different kr

Generate a full audio spectrum plane wave using the S/W/G module

In [1]:
import numpy as np
from sofia import gen, process, plot

from tqdm import tqdm_notebook

### Setup

In [2]:
pi = np.pi
r = 0.1      # Array radius
ac = 0       # Rigid Sphere
FS = 48000   # Sampling Frequency
NFFT = 128   # FFT-Bin
AZ = 0       # Azimuth angle
EL = pi / 2  # Elevation angle
Nsft = 5     # Transform order
Nrf = Nsft   # Radial filter order
Nviz = Nsft  # Visualization order
krIDX = [15, 23, 29, 39]  # kr-bin for subfigures

## Generate quadrature grid and weights

In [3]:
quadrature_grid, _ = gen.lebedev(110)

SOFiA Lebedev Grid


In [4]:
fftData, kr = gen.swg(r=r, gridData=quadrature_grid, ac=ac, FS=FS, NFFT=NFFT, AZ=AZ, EL=EL)

Segmented generator orders: 70 to 88
Progress: [##################################################] 100.0%

SOFiA I/T/C - Inverse spatial Transform Core R13-0306


## Spatial Fourier Transform

In [5]:
Pnm = process.stc(Nsft, fftData, quadrature_grid)

## Make radial filters

In [6]:
dn, _ = gen.mf(Nrf, kr, ac)

SOFiA M/F - Modal radial filter generator


## Generate data to visualize

In [7]:
N = kr.size

vizMtx = [None] * N

for k in range(0, N):
    vizMtx[k] = plot.makeMTX(Pnm, dn, Nviz, k)

    amtDone = k / (N - 1)
    print('\rProgress: [{0:50s}] {1:.1f}%'.format('#' * int(amtDone * 50), amtDone * 100), end="", flush=True)

Progress: [##################################################] 100.0%

In [14]:
for k in tqdm_notebook(range(0, N)):
    vizMtx[k] = plot.makeMTX(Pnm, dn, Nviz, k)

In [8]:
from plotly.offline import download_plotlyjs, init_notebook_mode
init_notebook_mode(connected=True)

from ipywidgets import interact, interactive, IntSlider

def viewShape(kr):
    plot.showTrace(plot.genVisual(vizMtx[kr], style='sphere'))

interact(viewShape, kr=IntSlider(min=0, max=(N - 1), step=1, continuous_update=False))

